In [0]:
# !pip install utils
import random


In [0]:
identity = lambda x: x

def argmin_random_tie(seq, key=identity):
    """Return a minimum element of seq; break ties at random."""
    # print("domain: ", seq)
    # print("key: ", key)
    return min(shuffled(seq), key=key)

def shuffled(iterable):
    """Randomly shuffle a copy of iterable."""
    items = list(iterable)
    random.shuffle(items)
    return items

def sudoku(puzzle):
    
    # add in checks to ensure set up is ok, e.g. 81 characters long
    
    rows = 'ABCDEFGHI'
    columns = '123456789'
    digits = '123456789'
    
    variables = cross(rows, columns)
    domains = dict(zip(variables, puzzle))
    
    for key, values in domains.items():
        if values == '.':
            domains[key] = list(digits)
        else:
            domains[key] = list(domains[key])
     

    
    unitlist = [cross(rows,a) for a in columns] + [cross(a, columns) for a in rows] + [cross(a,b) for a in ['ABC', 'DEF', 'GHI'] for b in ['123', '456', '789']]
    
    units = dict((s,[t for t in unitlist if s in t]) for s in variables)
    
    neighbours =  dict((s, set(units[s][0] +units[s][1]+ units[s][2]) - set([s])) for s in variables)
    
    constraints = lambda X, x, Y, y : x != y
    
    return variables, domains, neighbours, constraints

In [0]:
class CSP():
    def __init__(self, variables, domains, neighbours, constraints):
        self.variables = variables #list of variables
        self.domains = domains #dictionary where keys are variables
        self.neighbours = neighbours #dict: keys are variables, values are lists other variables in constraints with key
        self.constraints = constraints #function X,x,Y,y returns true if X = x, Y = y satisfy constraints
                                        #e.g. lambda X,x,Y,y : x != y
                        
    def prune(self, var, value):
        """ romove value val from domain of variable var """
        # print("helllloooohelllloooohelllloooohelllloooo")
        self.domains[var].remove(value)
        
    def assign(self, var, val, assignment):
        # print("assignassignassignassignassignassign")

        """ add variable var and value val to assigment """
        assignment[var] = val
        # self.domains[var].remove(val)
        
    def unassign(self, var, assignment):
        """ remove variable var from assignment """
        if var in assignment:
            del assignment[var]
           
    def nConflicts(self, var, val, assignment):
        """ return number of conflicts var = val has in assignent """
        count = 0
        for var2 in self.neighbours[var]:
            # print("This variable ", var, " has a neighbour ", var2)
            if var2 in assignment and not self.constraints(var, val, var2, assignment[var2]):
                # print(var, " and ", var2, " are conflicted ")
                count += 1
        return count
    
    def isGoalState(self, assignment):
        """ check is the current state a goal state """
    
        result = (len(assignment) == len(self.variables)) and (all(self.nConflicts(var, assignment[var], assignment) == 0 for var in self.variables))
        return result

    def conflicted_vars(self, current):
        """Return a list of variables in current assignment that are in conflict"""
        return [var for var in self.variables
                if self.nConflicts(var, current[var], current) > 0]


In [0]:
def min_conflicts(csp, max_steps=30000000):
    """Solve a CSP by stochastic Hill Climbing on the number of conflicts."""
    # Generate a complete assignment for all variables (probably with conflicts)
    csp.current = current = {}
    dont_change = []
    for domain in csp.domains:
        #print(domain, csp.domains[domain], len(csp.domains[domain]))
        if len(csp.domains[domain]) == 1:
          dont_change.append(domain)
    print ("Array of unchangables: ", dont_change)
    print("current - first", current)
    for var in csp.variables:
        if var in dont_change:
          # print("fixed", var, csp.domains[var])
          csp.assign(var, csp.domains[var][0], current)
          continue

        val = min_conflicts_value(csp, var, current)
        csp.assign(var, val, current)
    print("current - second", current)

    # Now repeatedly choose a random conflicted variable and change it
    # count_constant_cycles = 0
    previous_conflicts = {}
    for i in range(max_steps):
        conflicted = csp.conflicted_vars(current)
        # print("previous_conflicts ", set(previous_conflicts))
        # print("conflicted ", set(conflicted))
        
        currentConflictedString =  '-'.join(conflicted)

        if currentConflictedString in previous_conflicts:
            previous_conflicts[currentConflictedString] +=1
            if previous_conflicts[currentConflictedString] > 10000:
              break
        else:
            previous_conflicts[currentConflictedString] =1


        
        # if set(previous_conflicts) == set(conflicted):
        #     # print("wooowww")
        #     count_constant_cycles +=1
        # else:
        #     count_constant_cycles = 0
        # if count_constant_cycles > 10000:
        #     break

        # previous_conflicts = conflicted
        # print("conflicted", conflicted)
        if not conflicted:
            print("SOLVED: ", i)
            print("Iteration ", i, " conflicted: ", conflicted)
            print("Iteration ", i, " current: ", current)

            return current
        var = random.choice(conflicted)
        if var in dont_change:
          continue
        val = min_conflicts_value(csp, var, current)
        csp.assign(var, val, current)
        # a = input("enter a char to continue")
        if i%10000 == 0:
          print("Iteration ", i, " conflicted: ", conflicted)
          print("Iteration ", i, " current: ", current)
          print("Iteration ", i, " constant constraints: ", previous_conflicts)

    print("current - third", current)


    return False


def min_conflicts_value(csp, var, current):
    """Return the value that will give var the least number of conflicts.
    If there is a tie, choose at random."""
    # print(argmin_random_tie(csp.domains[var], key=lambda val: csp.nConflicts(var, val, current)))
    # print("current variable: ", var)

    return argmin_random_tie(csp.domains[var], key=lambda val: csp.nConflicts(var, val, current))



In [0]:
def cross(A,B):
    return [a+b for a in A for b in B]

In [0]:
example = "..3.2.6..9..3.5..1..18.64....81.29..7.......8..67.82....26.95..8..2.3..9..5.1.3.."

variables, domains, neighbours, constraints = sudoku(example)

In [0]:
print(variables)

['A1', 'A2', 'A3', 'A4', 'A5', 'A6', 'A7', 'A8', 'A9', 'B1', 'B2', 'B3', 'B4', 'B5', 'B6', 'B7', 'B8', 'B9', 'C1', 'C2', 'C3', 'C4', 'C5', 'C6', 'C7', 'C8', 'C9', 'D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'E1', 'E2', 'E3', 'E4', 'E5', 'E6', 'E7', 'E8', 'E9', 'F1', 'F2', 'F3', 'F4', 'F5', 'F6', 'F7', 'F8', 'F9', 'G1', 'G2', 'G3', 'G4', 'G5', 'G6', 'G7', 'G8', 'G9', 'H1', 'H2', 'H3', 'H4', 'H5', 'H6', 'H7', 'H8', 'H9', 'I1', 'I2', 'I3', 'I4', 'I5', 'I6', 'I7', 'I8', 'I9']


In [0]:
print(domains)

{'A1': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'A2': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'A3': ['3'], 'A4': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'A5': ['2'], 'A6': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'A7': ['6'], 'A8': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'A9': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B1': ['9'], 'B2': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B3': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B4': ['3'], 'B5': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B6': ['5'], 'B7': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B8': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'B9': ['1'], 'C1': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'C2': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'C3': ['1'], 'C4': ['8'], 'C5': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'C6': ['6'], 'C7': ['4'], 'C8': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'C9': ['1', '2', '3', '4', '5', '6', '7', '8', '9'], 'D1': ['

In [0]:
print(neighbours)

{'A1': {'A6', 'A9', 'C3', 'C1', 'A7', 'D1', 'A4', 'E1', 'B3', 'F1', 'I1', 'A3', 'G1', 'B1', 'A8', 'H1', 'C2', 'A5', 'B2', 'A2'}, 'A2': {'A6', 'A9', 'C3', 'A7', 'C1', 'G2', 'A4', 'E2', 'B3', 'D2', 'F2', 'A3', 'I2', 'B1', 'A8', 'A1', 'C2', 'H2', 'A5', 'B2'}, 'A3': {'A6', 'A9', 'C3', 'A7', 'C1', 'A4', 'H3', 'B3', 'I3', 'F3', 'G3', 'B1', 'D3', 'A1', 'A8', 'C2', 'A5', 'B2', 'E3', 'A2'}, 'A4': {'C5', 'B6', 'A6', 'A9', 'A7', 'G4', 'D4', 'E4', 'A3', 'F4', 'I4', 'H4', 'B5', 'A8', 'A1', 'C6', 'B4', 'A5', 'C4', 'A2'}, 'A5': {'C5', 'B6', 'A6', 'A9', 'A7', 'A4', 'H5', 'F5', 'A3', 'B5', 'A8', 'A1', 'G5', 'E5', 'C6', 'B4', 'C4', 'A2', 'I5', 'D5'}, 'A6': {'C5', 'B6', 'A9', 'A7', 'A4', 'F6', 'G6', 'H6', 'I6', 'E6', 'A3', 'B5', 'A8', 'D6', 'A1', 'C6', 'B4', 'A5', 'C4', 'A2'}, 'A7': {'B7', 'A6', 'A9', 'C7', 'G7', 'D7', 'A4', 'E7', 'I7', 'C9', 'B8', 'A3', 'B9', 'F7', 'A8', 'A1', 'C8', 'H7', 'A5', 'A2'}, 'A8': {'E8', 'B7', 'D8', 'A6', 'A9', 'C7', 'A7', 'H8', 'G8', 'A4', 'C9', 'I8', 'B8', 'A3', 'B9', 'F8', 

In [0]:
problem = CSP(variables, domains, neighbours, constraints)

In [0]:
while 1:
  test = min_conflicts(problem)
  if test != False:
    break

Array of unchangables:  ['A3', 'A5', 'A7', 'B1', 'B4', 'B6', 'B9', 'C3', 'C4', 'C6', 'C7', 'D3', 'D4', 'D6', 'D7', 'E1', 'E9', 'F3', 'F4', 'F6', 'F7', 'G3', 'G4', 'G6', 'G7', 'H1', 'H4', 'H6', 'H9', 'I3', 'I5', 'I7']
current - first {}
current - second {'A1': '9', 'A2': '5', 'A3': '3', 'A4': '6', 'A5': '2', 'A6': '8', 'A7': '6', 'A8': '4', 'A9': '1', 'B1': '9', 'B2': '8', 'B3': '4', 'B4': '3', 'B5': '7', 'B6': '5', 'B7': '2', 'B8': '1', 'B9': '1', 'C1': '6', 'C2': '1', 'C3': '1', 'C4': '8', 'C5': '4', 'C6': '6', 'C7': '4', 'C8': '9', 'C9': '3', 'D1': '3', 'D2': '9', 'D3': '8', 'D4': '1', 'D5': '6', 'D6': '2', 'D7': '9', 'D8': '5', 'D9': '7', 'E1': '7', 'E2': '6', 'E3': '5', 'E4': '4', 'E5': '3', 'E6': '9', 'E7': '1', 'E8': '8', 'E9': '8', 'F1': '2', 'F2': '4', 'F3': '6', 'F4': '7', 'F5': '8', 'F6': '8', 'F7': '2', 'F8': '3', 'F9': '5', 'G1': '5', 'G2': '3', 'G3': '2', 'G4': '6', 'G5': '1', 'G6': '9', 'G7': '5', 'G8': '7', 'G9': '4', 'H1': '8', 'H2': '7', 'H3': '9', 'H4': '2', 'H5': '5'

In [0]:
print(domains)

In [0]:
domains